In [1]:
import numpy as np
import pandas as pd
from matplotlib import pyplot as plt
import tifffile as tf
from scipy.ndimage.filters import gaussian_filter1d as gaussian
from glob import glob
from scipy.signal import savgol_filter, medfilt
import matplotlib.ticker as ticker
from scipy.optimize import curve_fit

In [2]:
# 1. load data into pandas data frame

# 2. convert data from I(t) to c_i(t) via equation for G quadruplex binding
    # - find t0
    # - 
# 3. calculate dc_i/dt for each GUV

# 4. calculate background intensity and convert this to c_0(t) via g quadruplex binding model

# 5. plot dc_/dt/A_GUV vs c_0-c_i (expect to see a positive linear relationship)


# as data includes actual G4 background for GUV permeability and later Gramicidin A experiments, start with these experiments


In [3]:
App = 3.16 #um^2
Amin= 75*App*1e-12 #m^2


# G quadruplex model binding



def exp_I(t,k,c):
    
    k_b = 8.8
    A = 1
#     c = 0.98
#     c = 0.46
    return c+(1-c)/(A*k_b*(1-np.exp(-k*t))**2+1)


def inv(I, k = 8.8,A = 0.5):
    
    if I > 1:
        return 0
    
    elif I < A:
        return 1
        
    else:
        return np.sqrt((1/k)*((1-A)/(I-A)-1))

#smoothing configs

sigma = 30




# Calibration model fit


## **If you have already fitted a calibration function and saved the parameters skip this section**

## Discussion of binding model deficiencies

1. **Binding model**

By considering the binding reaction G4 + nK <=> complex we can develop a model to fit the calibration experiment for the g quadruplex sensor.

It was found that in an excess of potassium the 'completely folded' g quadruplex goes to 0.5 of its free intensity. I assume then that in the intermediate concentrations of potassium, there is a mixture of unfolded and folded g quadruplex. 

Therefore $I = I_0[G4]_{free} + 0.5I_0[G4]_{folded}$,

by assuming on the addition of potassium the system reaches equilibrium much faster than the timescales of the transport, then we gain  $\frac{I}{I_0} = 0.5(\frac{1}{1+K_b[K]^2} +1)$

$K_b$ is found by fitting this function to the calibration.

2. **Problems**

As this function plateaus at 0.5, defining a sensible inverse that can practicably applied to a noisy intensity measurement (to measure [K]  is difficult. As noisy variations near $\frac{I}{I_0}$ cause wild swings in the concentration.

3. **Solution**

Therefore we surpress these swings by defining an approximate inverse that does not diverge at the edges.

We do this by creating an effective intensity of the folded g quadruplex that is artificially lower than the believe value. Therefore our calibration model becomes:

$I = I_0[G4]_{free} + c_{eff}I_0[G4]_{folded}$, where $c_{eff} < 0.5$.
    
$\frac{I}{I_0} = c_{eff} + \frac{1-c_{eff}}{K_b[K]^2 +1}$

**This doesn't really work as we still have a blowing up value, need to define a nicer function**

Define a polynomial approximation that is similar

In [4]:
# finding a suitable calibration

calib_data = pd.read_csv('../20210323_KCLFAMG4Q0to20mMCalib/RelIntensG41Concentration.csv')

In [9]:
%matplotlib qt
I= np.linspace(1,0.2,100)

fig, ax = plt.subplots(1,1)

ax.scatter(calib_data['Rel. Intes'],calib_data['K conc [mM]'],marker = '+',s = 5)

legend = []

# fit a polynomial


fit = np.polyfit(-np.log(calib_data['Rel. Intes'].iloc[:-1]),calib_data['K conc [mM]'].iloc[:-1],3)

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c



ax.plot(I,fit_func(I,fit))

legend.append('Calibration')

def model_fit(cK,kb,c):
    return c + (1-c)/(kb*cK**2+1)

params = curve_fit(model_fit,calib_data['K conc [mM]'],calib_data['Rel. Intes'], p0 = [8.8,0.45])

cK_bar = np.linspace(0,2)
I_bar = model_fit(cK_bar,params[0][0],params[0][1])

ax.set_xlim([0.35,1.05])
ax.plot(I_bar,cK_bar,label = 'Model')
legend.append('Model')

l  = plt.errorbar(calib_data['Rel. Intes'],calib_data['K conc [mM]'],rel_errorK*calib_data['K conc [mM]'],drelI,c = 'k')

ax.set_xticks([0.4,0.6,0.8,1])
ax.set_xticklabels([0.4,0.6,0.8,1],fontsize  = 15)

ax.set_yticks([0,1,2])
ax.set_yticklabels([0,1,2],fontsize = 15)
ax.set_ylim([-0.1,2.1])
plt.tick_params(direction = 'in',top = True,bottom = True,right = True, left = True,length = 5)
ax.set_xlabel('Rel Intensity [a.u]',fontsize = 18)
ax.set_ylabel('[K]/[mM]',fontsize = 18)
l[0].remove()
plt.legend(legend)



3
2
1
0


In [30]:
help(l.remove)

Help on method remove in module matplotlib.container:

remove() method of matplotlib.container.ErrorbarContainer instance



# Errors in calibration

**Errors are mainly due to the focal plane measured**


In [6]:
raw_data = pd.read_csv('../20210323_KCLFAMG4Q0to20mMCalib/1uM/Intensities0-2mM.csv')

In [7]:
n = 512**2

print(raw_data['StdDev']/np.sqrt(n))

dI = raw_data['StdDev']/np.sqrt(n)
drelI = dI/raw_data['Mean']

drelI = drelI*10

0    2.244234
1    2.140793
2    1.921438
3    1.709535
4    1.638162
5    1.617246
Name: StdDev, dtype: float64


# Potassium concentration errors

In [8]:
rel_errorK = 0.02



# Load calibration function parameters and define function



In [4]:
fitsdf = pd.read_csv('../Calibrations/Calibration_approx_fit_params.csv')

fit = fitsdf['Fitting Params']

def fit_func(I,fit):
    
    c = np.zeros_like(I)
    
    for i in range(1,len(fit)+1):

        c += fit[i-1]*(-np.log(I))**(len(fit)-i)
        print(len(fit)-i)
    return c


# Single GUV modelling

In [11]:
t0 = 49
t1 = -1
dt = 15/60

In [17]:
# load 260pM Gramicidin A experiment

dfI = pd.read_csv('../KineticsofLeakageGramicidin/collatedIabs260pM.csv')
dfA = pd.read_csv('../KineticsofLeakageGramicidin/collatedIabs260pM.csv')

In [18]:
dfI = dfI.iloc[:,1:]
dfA = dfA.iloc[:,1:]

In [19]:
dfA = dfA.fillna(0)
dfI = dfI.fillna(0)

# Remove small detected objects, most likely not GUVs

**check that the size is appropriate for the experiment**

In [9]:
# remove traces for GUVs below a certain area

for col in dfI.columns:
    
    if col in dfA.columns:
        area = 1e-12*App*np.mean(dfA[col].iloc[:30])
        
        if area < Amin:
            dfI.pop(col)
            dfA.pop(col)

# Remove intensity curves with sudden drops
## These are likely from GUVs suddenly escaping the trap

In [13]:

def remove_burst_events(data,threshold = 0.45):
    
    for column in data.columns:
        
        if len(data[column][data[column] < threshold]) >=1:
            data.pop(column)
            

In [21]:
%matplotlib qt
fig, ax = plt.subplots(1,1)

for col in dfI.columns:
    ax.plot(dfI[col].iloc[t0:])

In [20]:
# normalise intensities

for col in dfI.columns:
    dfI[col] = dfI[col]/np.mean(dfI[col][:30])
remove_burst_events(dfI)

# Smooth data

## Smoothing strategy

1. In experiments where there was relatively fast decay in intensity initially, but slows down (as exponential decays do..), yet there is still a lot of noise, it may be necessary to smooth different regions with different 'cutoff's.
When the intensity has dropped, the signal to noise drops. What's more during the slower period of intensity decay, there is increasing likelihood that some long timescale event will have happened to distort the data. This long timescale noise may be of a similar timescale to the 'signal' in the early period of rapid decay. 

2. The **solution** chosen here, is to have the user select a timepoint to bisect the time traces. The early period up until that timepoint is smoothed with the 1st user input smoothing parameter (usually between 11-21). Then the later period of slow decay is smoother with much larger smoothing settings (50-80). In order to ensure a smooth 'stitching' of these differently smoothed traces, we concatenate and repeat the smoothing with the smallest of the two specified smoothing parameters.

In [22]:
def smooth_decay(I,t0,t1=-1,smoothing_0 = 51,smoothing_1 = 81):
    
    
    if smoothing_0 > t1-t0 and t1 != -1:
        raise ValueError('Smoothing parameter cannot be greater than input data')
    
    smoothed_decay_0 = I.iloc[t0:t1]
    
    smoothed_decay_0 = savgol_filter(smoothed_decay_0,smoothing_0,1)
    
    if t1 != -1:
        
        smoothed_decay_1 = I.iloc[t1:]
        smoothed_decay_1  = savgol_filter(smoothed_decay_1,smoothing_1,1)
        
        smoothed_decay = np.concatenate((smoothed_decay_0,smoothed_decay_1))
    else:
        smoothed_decay = smoothed_decay_0
                               
    final_smoothed_decay = savgol_filter(smoothed_decay,smoothing_0,1)
    return final_smoothed_decay
                                   

In [24]:
#Check smoothing still fits data
#
num = 8
fig,axs = plt.subplots(1,num)

for i,col in enumerate(dfI.columns[np.random.randint(0,len(dfI.columns),num)]):
    #
    axs[i].plot(dfI[col].iloc[t0:].to_numpy())
    
    axs[i].plot(smooth_decay(dfI[col],t0,t1 = 430,smoothing_0=51,smoothing_1=101))
    

# Use calibration inverse to convert I to [K]

In [25]:
dfC_dict = {}

# can't exploit numpy broadcasting

for col in dfI.columns:
    
    smoothed_decay = smooth_decay(dfI[col],t0,t1 = 430,smoothing_0=51,smoothing_1=101)
#     print(smoothed_decay)
#     normalised_sd = smoothed_decay/np.mean(smoothed_decay[:30])
    
    cs = []
    for I in smoothed_decay:
#         print(I)
        cs.append(fit_func(I,fit))
    
    
    dfC_dict[col] = cs
    
dfC = pd.DataFrame(dfC_dict)

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


...

3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3


1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2
1
0
3
2


In [69]:
%matplotlib qt

fig, axs = plt.subplots(1,3)

t = dt*np.arange(0,len(dfC))
for col in dfC.columns:
    
    
    axs[0].plot(t,dfC[col])
#     axs[1].plot(t,medfilt(dfI[col].iloc[t0:t1],31))
    axs[2].plot(t,dfI[col].iloc[t0:t1])

    for ax in axs:
        ax.set_ylim([0,1])



In [70]:
# find representative background concentration variation

# tifs = glob('/media/marcus/9C33-6BBD/20210920_GramA_260pM07_3nM815_1mMKCl_1/260pM/*.tif')

# bgs = []

# fig, ax = plt.subplots(1,1)

# for tif in tifs:
    
#     vid = tf.TiffFile(tif)
    
#     frames = vid.asarray()
    
#     bg = np.median(frames,axis  =(1,2))
#     bg = np.array(bg)/np.max(bg)
#     bgs.append(bg)
    
    
#     ax.plot(bg)

# This confirms that the normalised background is the same for each chamber. Suggesting potassium concs are identical between chambers



In [36]:
# filter concentration data by gradient
# if 

fig, axs = plt.subplots(1,2)

for col in dfC.columns:
    
    grad = np.gradient(dfC[col])
    
    if len(grad[grad <= -0.0009])/len(grad) > 0.05:
        dfC.pop(col)
        continue
    axs[0].hist(grad,15)
    axs[1].plot(dfC[col])

In [58]:
tifs = glob('/media/marcus/9C33-6BBD/20210427_OmpF_PCPG_KCL_Flush_2-20210427T184510Z-002/20210427_OmpF_PCPG_KCL_Flush_2/*.tif')
tif = tifs[-1]

vid = tf.TiffFile(tif)

frames = vid.asarray()
bg = np.median(frames,axis = (1,2))

bg = np.array(bg)-np.mean(bg[:30])
bg = bg/np.max(bg)

smoothed_bg = medfilt(bg,11)

OME series: not an ome-tiff master file


In [131]:
# c_bg = []
# for x in bg[360+t0:]:
#     c_bg.append(inv(x))

In [132]:
# fig, axs = plt.subplots(1,2)


# smoothed_background = gaussian(c_bg,sigma)
# axs[0].plot(smoothed_background)
# axs[1].plot(bg[360+t0:])

In [80]:
# drift in the background intensity over time, once the potassium has arrived, is causing a drifting predicted potassium concentration
# this is unlikely to be the case in reality.
# Therefore the best thing may be to just assume that after an initial 80 frame boundary region (20 mins) for this exp
# the potassium concentration externally reaches 1mM.


In [37]:
# calculating c_ext - c_i

dfdeltaC_dict = {}

for col in dfC:
    
    dfdeltaC_dict[col] = 1-dfC[col]
    
dfdeltaC = pd.DataFrame(dfdeltaC_dict)

In [38]:
fig, axC = plt.subplots(1,1)

delete_cols = []

for col in dfdeltaC.columns:
    graddeltaC = np.gradient(dfdeltaC[col])
    
    
#     if len(graddeltaC[graddeltaC > 0]) > 1:
#         delete_cols.append(col)
#         continue
        
    axC.plot(dfdeltaC[col])

In [39]:
for col in delete_cols:
    dfdeltaC.pop(col)

In [40]:
# now calculate J

# J = (1/A)*dN/dt = R/3* dc_i/dt

dfJ_dict = {}


for col in dfdeltaC:
    
    if col in dfA:
        print(col)
        delta_c = np.gradient(dfC[col],dt)/60 #molm^-3s^-1
        print(dfC[col])
        A = np.mean(dfA[col].iloc[:30])*App*1e-12 #m^2
#         if A < Amin:
#             continue
        R = np.sqrt(A/np.pi) #m
        
        dfJ_dict[col] = R/3*delta_c #molm^-2s^-1
        

dfJ = pd.DataFrame(dfJ_dict)




11003
0       -0.014215430117656962
1       -0.013531538181427678
2       -0.012848307755151965
3       -0.012165738652939788
4       -0.011483830687592312
5       -0.010802583670595813
6       -0.010121997412119218
7       -0.009442071721009797
8        -0.00876280640478887
9       -0.008084201269649302
10      -0.007406256120449347
11      -0.006728970760710133
12       -0.00605234499261131
13       -0.00537637861698668
14      -0.004701071433321629
15       -0.00402642323974694
16      -0.003352433833036195
17     -0.0026791030086011905
18     -0.0020064305604885896
19     -0.0013344162813745952
20     -0.0006630599625622995
21      7.638606023845605e-06
22      0.0006776796358407087
23      0.0013470633397318476
24        0.00201578993193111
25      0.0026838596280667733
26      0.0032713548987213315
27       0.003822946085730518
28      0.0043734793634686965
29       0.004925377909582098
                ...          
521       0.06311687614730856
522        0.0630313238717419
523 

Name: 14013, Length: 551, dtype: object
14014
0        -0.02566207470036083
1        -0.02472848598015193
2       -0.023796096790291345
3        -0.02286490672960358
4        -0.02193491539283948
5       -0.021006122370661327
6       -0.020078527249625742
7        -0.01915212961216861
8       -0.018226929036586386
9        -0.01730292509702055
10       -0.01638011736344204
11      -0.015458505401632319
12      -0.014538088773167649
13      -0.013618867035403343
14      -0.012700839741454594
15       -0.01178400644018096
16      -0.010868366676168539
17      -0.009953919989714285
18      -0.009040665916806632
19      -0.008128603989109287
20      -0.007217733733944981
21      -0.006308054674275874
22      -0.005399566328687527
23     -0.0044922682113706204
24     -0.0035861598321047746
25      -0.002681240696237979
26      -0.001789745856475174
27     -0.0008955386684291917
28     1.5205581543447852e-05
29       0.000927831393009327
                ...          
521       0.234312166163

In [46]:
fig, axs = plt.subplots(1,3)
legend = []

for col in dfJ.columns:

    legend.append(col)
#     print(dfdeltaC)

    axs[0].scatter(dfdeltaC[col],dfJ[col]*1e10, marker = '+', s = 10)
    print(dfJ[col])

    axs[1].plot(dt*np.arange(0,len(dfC[col])),dfC[col])

    
#     gradients = []
#     win = 10
#     for i in range(dfJ[col].shape[0]-(win-1)):
        
#         gradient = np.mean(np.gradient(dfJ[col].iloc[i:i+win]))
#         gradients.append(gradient)
        
    
    axs[2].plot(np.gradient(dfJ[col],dfdeltaC[col]))
axs[0].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[1].tick_params(direction = 'in',left = True,right = True,bottom = True,top = True,length = 6)
axs[0].set_xlabel('[K_ext]-[K_int] [mM]',fontsize = 18)

axs[0].set_ylabel('J [molm^-2s^-1]',fontsize = 18)

axs[1].set_ylabel('[K_int] [mM]',fontsize = 18)


axs[1].set_xlabel(' T [mins]',fontsize = 18)


#xticks

axs[0].set_xticks([0,0.5,1])
axs[0].set_xticklabels([0,0.5,1],fontsize = 15)
axs[0].set_xlim([0,1.05])

axs[1].set_xticks([0,60,120])
axs[1].set_xticklabels([0,60,120],fontsize = 15)

#yticks

axs[0].set_yticks([0,0.01,0.02])
axs[0].set_yticklabels([0,0.01,0.02],fontsize = 15)

axs[0].set_ylim([-0.0005,0.0105])
axs[1].set_yticks([0, 0.5,1])
axs[1].set_yticklabels([0,0.5,1],fontsize = 15)


axs[0].set_ylim([-0.0005,0.0205])
axs[1].set_ylim([-0.05,1.05])


plt.legend(legend)
# plt.rcParams['text.usetex'] = True

# def myticks(x,pos):

#     if x == 0: return "$0$"

#     exponent = int(np.log1

#     coeff = x/10**exponent

#     return r"${:2.0f} \times 10^{{ {:2d} }}$".format(coeff,exponent)

# axs[0].yaxis.set_major_formatter(ticker.FuncFormatter(myticks))

0      2.729870e-10
1      2.729050e-10
2      2.727410e-10
3      2.725771e-10
4      2.724132e-10
5      2.722493e-10
6      2.720855e-10
7      2.719217e-10
8      2.717580e-10
9      2.715942e-10
10     2.714306e-10
11     2.712669e-10
12     2.711033e-10
13     2.709397e-10
14     2.707762e-10
15     2.706126e-10
16     2.704492e-10
17     2.702857e-10
18     2.701223e-10
19     2.699589e-10
20     2.697956e-10
21     2.696323e-10
22     2.694690e-10
23     2.693058e-10
24     2.691426e-10
25     2.752324e-10
26     2.737056e-10
27     2.614343e-10
28     2.583785e-10
29     2.660388e-10
           ...     
504   -5.515482e-11
505   -5.109900e-11
506   -5.413169e-11
507   -6.430045e-11
508   -7.472197e-11
509   -8.189723e-11
510   -8.191431e-11
511   -8.193138e-11
512   -8.194846e-11
513   -8.196555e-11
514   -8.198263e-11
515   -8.199972e-11
516   -8.201680e-11
517   -8.203389e-11
518   -8.205099e-11
519   -8.206808e-11
520   -8.208518e-11
521   -8.210227e-11
522   -8.211937e-11


0      1.109256e-09
1      1.108426e-09
2      1.106766e-09
3      1.105106e-09
4      1.103448e-09
5      1.101789e-09
6      1.100132e-09
7      1.098474e-09
8      1.096818e-09
9      1.095162e-09
10     1.093507e-09
11     1.091852e-09
12     1.090198e-09
13     1.088545e-09
14     1.086892e-09
15     1.085240e-09
16     1.083589e-09
17     1.081939e-09
18     1.080289e-09
19     1.078639e-09
20     1.076991e-09
21     1.075343e-09
22     1.073696e-09
23     1.072050e-09
24     1.070404e-09
25     9.916413e-10
26     9.142695e-10
27     9.047113e-10
28     8.925104e-10
29     8.701228e-10
           ...     
504    3.042087e-10
505    2.971692e-10
506    3.062713e-10
507    3.098719e-10
508    3.310653e-10
509    3.494205e-10
510    3.491602e-10
511    3.489001e-10
512    3.486405e-10
513    3.483812e-10
514    3.481223e-10
515    3.478637e-10
516    3.476056e-10
517    3.473477e-10
518    3.470903e-10
519    3.468332e-10
520    3.465765e-10
521    3.463202e-10
522    3.460642e-10


0      3.524594e-11
1      3.524512e-11
2      3.524349e-11
3      3.524185e-11
4      3.524022e-11
5      3.523859e-11
6      3.523696e-11
7      3.523532e-11
8      3.523369e-11
9      3.523206e-11
10     3.523043e-11
11     3.522880e-11
12     3.522716e-11
13     3.522553e-11
14     3.522390e-11
15     3.522227e-11
16     3.522063e-11
17     3.521900e-11
18     3.521737e-11
19     3.521574e-11
20     3.521411e-11
21     3.521247e-11
22     3.521084e-11
23     3.520921e-11
24     3.520758e-11
25     1.203829e-11
26    -1.301187e-11
27    -1.227995e-11
28     4.332002e-13
29     1.929345e-11
           ...     
504   -1.471087e-10
505   -1.567285e-10
506   -1.698454e-10
507   -1.771796e-10
508   -1.734401e-10
509   -1.678485e-10
510   -1.678912e-10
511   -1.679339e-10
512   -1.679766e-10
513   -1.680193e-10
514   -1.680621e-10
515   -1.681048e-10
516   -1.681475e-10
517   -1.681903e-10
518   -1.682330e-10
519   -1.682757e-10
520   -1.683185e-10
521   -1.683613e-10
522   -1.684040e-10


0     -6.453356e-10
1     -6.456530e-10
2     -6.462878e-10
3     -6.469228e-10
4     -6.475580e-10
5     -6.481934e-10
6     -6.488290e-10
7     -6.494648e-10
8     -6.501008e-10
9     -6.507370e-10
10    -6.513734e-10
11    -6.520100e-10
12    -6.526467e-10
13    -6.532837e-10
14    -6.539208e-10
15    -6.545582e-10
16    -6.551957e-10
17    -6.558333e-10
18    -6.564712e-10
19    -6.571093e-10
20    -6.577475e-10
21    -6.583859e-10
22    -6.590245e-10
23    -6.596632e-10
24    -6.603021e-10
25    -8.269866e-10
26    -9.816951e-10
27    -9.500616e-10
28    -9.193769e-10
29    -8.006358e-10
           ...     
504    5.022455e-11
505    5.849628e-11
506    1.650184e-10
507    3.559881e-10
508    4.640286e-10
509    4.763155e-10
510    4.758838e-10
511    4.754524e-10
512    4.750213e-10
513    4.745904e-10
514    4.741598e-10
515    4.737295e-10
516    4.732995e-10
517    4.728698e-10
518    4.724404e-10
519    4.720112e-10
520    4.715824e-10
521    4.711538e-10
522    4.707256e-10


0      1.087971e-10
1      1.087849e-10
2      1.087606e-10
3      1.087362e-10
4      1.087119e-10
5      1.086876e-10
6      1.086633e-10
7      1.086390e-10
8      1.086147e-10
9      1.085903e-10
10     1.085660e-10
11     1.085417e-10
12     1.085174e-10
13     1.084931e-10
14     1.084688e-10
15     1.084445e-10
16     1.084202e-10
17     1.083959e-10
18     1.083716e-10
19     1.083474e-10
20     1.083231e-10
21     1.082988e-10
22     1.082745e-10
23     1.082502e-10
24     1.082259e-10
25     1.088333e-10
26     1.222438e-10
27     1.312765e-10
28     1.368090e-10
29     1.412054e-10
           ...     
504    1.985365e-10
505    2.034566e-10
506    2.099574e-10
507    2.044698e-10
508    1.948969e-10
509    1.906436e-10
510    1.905517e-10
511    1.904601e-10
512    1.903687e-10
513    1.902775e-10
514    1.901866e-10
515    1.900959e-10
516    1.900055e-10
517    1.899153e-10
518    1.898253e-10
519    1.897356e-10
520    1.896461e-10
521    1.895569e-10
522    1.894679e-10


0     -1.355174e-10
1     -1.355307e-10
2     -1.355572e-10
3     -1.355838e-10
4     -1.356103e-10
5     -1.356369e-10
6     -1.356635e-10
7     -1.356900e-10
8     -1.357166e-10
9     -1.357432e-10
10    -1.357698e-10
11    -1.357963e-10
12    -1.358229e-10
13    -1.358495e-10
14    -1.358761e-10
15    -1.359027e-10
16    -1.359292e-10
17    -1.359558e-10
18    -1.359824e-10
19    -1.360090e-10
20    -1.360356e-10
21    -1.360622e-10
22    -1.360888e-10
23    -1.361154e-10
24    -1.361420e-10
25    -1.306582e-10
26    -1.240460e-10
27    -1.244443e-10
28    -1.172060e-10
29    -1.116571e-10
           ...     
504    1.803958e-10
505    1.779004e-10
506    1.796433e-10
507    1.944899e-10
508    2.136069e-10
509    2.247532e-10
510    2.246739e-10
511    2.245946e-10
512    2.245153e-10
513    2.244360e-10
514    2.243568e-10
515    2.242775e-10
516    2.241983e-10
517    2.241190e-10
518    2.240398e-10
519    2.239606e-10
520    2.238814e-10
521    2.238022e-10
522    2.237230e-10


In [64]:
%matplotlib qt
figJ, axJ = plt.subplots(1,1)
figC, axC = plt.subplots(1,1)



def Jfit(deltac,k,c):
    return k*deltac + c

p0 = [1e-14,0]
Pparams = {}
cols = []

legend = []
for i,col in enumerate(dfJ.columns):
    

    t = dt*np.arange(0,len(dfC[col]))
    
    J = dfJ[col].iloc[t > 0]
    deltaC = dfdeltaC[col].iloc[t > 0]
    
#     deltaC_bar = np.linspace(dfC[col].min(),1)
    params = curve_fit(Jfit,deltaC.iloc[deltaC.to_numpy().astype(float)>0.85],J.iloc[deltaC.to_numpy().astype(float)>0.85],p0)    
    J_bar = Jfit(deltaC.iloc[deltaC.to_numpy().astype(float)>0.85],*params[0])
    P = params[0][0]
    dP = np.sqrt(params[1][0][0])
    print(dP/P, P)
    

    
    if  P < 0:
        dfJ.pop(col)
        
        dfdeltaC.pop(col)        
        continue
        
    Pparams[col] = params
    if len(J.iloc[(deltaC < 0.75).to_numpy()]) < 1:
        dfJ.pop(col)
        
        dfdeltaC.pop(col)         
        continue
        
    if col == '10009':
        continue
    ####################
    # just for this particular case need to filter out a specific trace 
    #
    legend.append(col)
    
#     if len(J_arr[J_arr < 0.5 ]) >=1:
#         continue
        
    Pparams[col] = params
    cols.append(col)
   
    # plot fluxes
    axJ.scatter(deltaC,J,alpha = 0.25)
    axJ.plot(deltaC.iloc[deltaC.to_numpy().astype(float)>0.85],J_bar)
    
    #plot the Intensity vs time
    
    axC.plot(t,dfC[col])
 
#Flux plot params


axJ.set_xticks([0,0.5,1])
axJ.set_xlim([-0.05,1.05])
axJ.set_xticklabels([0,0.5,1],fontsize = 15)

axJ.set_xlabel('$[K]_{ext} - [K]_{in}$ [mM]',fontsize = 18)
axJ.set_yticks([0,5e-9,1e-8,1.5e-8])
axJ.set_yticklabels([0,5,10,15],fontsize = 15)

axJ.set_ylim([-1e-9,16e-9])
#  
    
axJ.set_ylabel('J  [$10^{-9}$ mol$m^{-2}s^{-1}$]',fontsize = 18)
axJ.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

axC.set_xticks([0,20,40])
axC.set_xticklabels([0,20,40],fontsize = 15)
axC.set_xlabel('Time [mins]',fontsize = 18)
axC.set_xlim([-2,45])
axC.set_yticks([0,0.5,1])
axC.set_yticklabels([0,0.5,1],fontsize = 15)
axC.set_ylabel('Rel I',fontsize = 18 )
axC.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)
axC.set_ylim([-0.05,1.05])

# plt.legend()
# global params

# plt.tick_params(direction = 'in',left = True,right = True, top = True, bottom = True,length = 7)

0.0690884418971863 3.5874178059659402e-09
0.05163549796405269 4.275392489219876e-09
0.05012541584288574 8.286516076819595e-09
0.15046111299416595 6.563365437967872e-10
0.07392616384480537 2.3259868222583032e-09
0.06286929425626192 1.6096171066408063e-09
0.10233768929609888 4.540253811174546e-09
0.18411620674594958 1.8888678915851546e-09
6.423499233866576 2.038462473467277e-11
0.0786711239845626 3.914720042087798e-09
0.08182542706910759 4.627255120553094e-09
0.04841590261153261 4.363090407320677e-09
0.031624918533994746 2.0741705200680667e-08
0.06154160733951286 9.55245997971314e-09
0.10694772492711117 2.3892143984653153e-09
0.08381478694003265 2.888567371359049e-09
0.49736943748176565 3.9197338313666025e-10
0.12661607467451452 9.805383074495785e-10
0.35773356249972543 8.329983105727797e-10
0.12473059641416528 2.8844023798437935e-09
0.04632873554257366 5.5415157979075064e-09
0.04294987013737044 8.33182268510466e-09
0.17034105442175443 1.045951277122747e-09
0.020547102905632723 8.0869069

(-0.05, 1.05)

# Save permeability values


In [65]:
P_df = {'P ms^-1': [Pparams[key][0][0] for key in Pparams.keys()],
       'dP/P': [np.sqrt(Pparams[key][1][0][0])/Pparams[key][0][0] for key in Pparams.keys()],
       'A':[np.mean(dfA[key].iloc[:30]) for key in Pparams.keys()]}
        
P_identified = {key:[Pparams[key][0][0]] for key in Pparams.keys()}
P_df = pd.DataFrame(P_df)
P_identified = pd.DataFrame(P_identified)
P_df['P cms^-1'] = P_df['P ms^-1']*100

P_df.to_csv('Permeabilities_GramicidinA_260pM20210920.csv')

# Save Flux vs deltaC data

In [61]:
dfJ.to_csv('Flux_GramA_260pM_20210920.csv')
dfdeltaC.to_csv('deltaC_GramA_260pM_20210920.csv')
P_identified.to_csv('PbyGUVId_GramA_260pM_20210920.csv')

# The relationship between J and delta c

The variation of the flux, J, with $\Delta c$ is linear. However in order to gain a good fit, we have to relax ths condition that the flux is zero when the gradient is 0. 

Near to 1mM internal concentration the calibration underestimates the internal concentration. Therefore it overestimates the concentration gradient at the point of zero flux. This develops an associated error in the y intercept and the permeability.


In [51]:
JoverP = {}

for col in Pparams.keys():
    
    P = Pparams[col][0][0]
    dP = np.sqrt(Pparams[col][1][0][0])
    
    if dP/P > 0.1 or P < 0:
        
        continue
    
    JoverP[col] = dfJ[col]/P
    
dfJoverP = pd.DataFrame(JoverP)


fig, ax = plt.subplots(1,1)

for col in dfJoverP.columns:
    
    ax.scatter(dfdeltaC[col],dfJoverP[col])
    

In [156]:
axs[2].cla()

# Mean J vs Mean concentration difference

Need to bin the concentration differences and then average the flux within each bin


In [59]:
deltaCbins = np.linspace(0.5,1,20)

deltaC_arr = dfdeltaC[cols].to_numpy()

dfJoverP = dfJ[cols]

for col in dfJoverP.columns:
    dfJoverP[col] = dfJoverP[col].to_numpy()/P_identified[col].iloc[0]
    
    
J_arr = dfJoverP.to_numpy()

J_mean = []
deltaC_mean = []

for i in range(len(deltaCbins)-1):
    
    deltaC_mean.append(np.median(deltaC_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])]))
    J_mean.append(np.median(J_arr[(deltaC_arr < deltaCbins[i+1]) * (deltaC_arr >deltaCbins[i])]))


/home/marcus/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [60]:
figm,axm = plt.subplots(1,1)


axm.scatter(deltaC_mean,J_mean)
# axm.set_ylim([-1e-9,16e-9])